In [5]:
!pip install nltk
!pip install pandas
!pip install text2num
!pip install scikit-learn
!pip install tqdm
!pip install beautifulsoup4


[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


   ---------------------------------------- 0.0/59.2 kB ? eta -:--:--
   ------ --------------------------------- 10.2/59.2 kB ? eta -:--:--
   -------------------- ------------------- 30.7/59.2 kB 445.2 kB/s eta 0:00:01
   ---------------------------------------- 59.2/59.2 kB 526.7 kB/s eta 0:00:00



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: C:\Users\Rog\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [1]:
from nltk.tokenize import word_tokenize
import pandas as pd
import re
from text_to_num import text2num
from collections import Counter
from sklearn.model_selection import train_test_split
import os
import pandas as pd
import re
import logging
from tqdm import tqdm
import os
import xml.etree.ElementTree as ET
from bs4 import BeautifulSoup
from collections import defaultdict

# Lectura de data_reading_20N

In [7]:
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

In [8]:
def clean_body(content):
    """
    Limpia el contenido del cuerpo del correo eliminando saltos de línea (\n)
    y tabulaciones (\t), dejando solo espacios.
    """
    content = content.replace("\n", " ").replace("\t", " ").strip()
    content = re.sub(r"\s+", " ", content)  # Reemplazar múltiples espacios por uno solo
    return content


Primero debemos limpiar el contenido del cuerpo que tiene el correo, eliminando los saltos de linea y tabulaciones que existen dentro del archivo, dejando solo esto por espacios.

In [9]:
def extract_email_parts(file_content):
    """
    Extrae las partes 'From', 'Subject' y el 'Body' del archivo.
    Si 'Subject' está ausente, el 'Body' comienza inmediatamente después de que se tienen ambos.
    """
    # Buscar la línea que contiene "From:"
    from_match = re.search(r"From:\s*(.*)", file_content)
    
    # Buscar la línea que contiene "Subject:" (puede contener diferentes prefijos)
    subject_match = re.search(r"Subject:\s*(.*)", file_content, re.IGNORECASE)
    
    # Inicializamos el contenido de las partes
    from_part = None
    subject_part = None
    body_part = None
    
    # Si encontramos "From"
    if from_match:
        from_part = from_match.group(1).strip()
        
        # Si encontramos también el "Subject"
        if subject_match:
            subject_part = subject_match.group(1).strip()
            
            # El Body comienza después del primer salto de línea tras el Subject
            body_start = file_content.find("\n", subject_match.end())
        else:
            # Si no hay Subject, el Body comienza justo después del "From"
            body_start = file_content.find("\n", from_match.end())
        
        # Extraer el body desde el punto donde empieza
        body_part = file_content[body_start:].strip()

        # Asegurarse de que el `From` no está duplicado en el Body
        body_part = body_part.replace(f"From: {from_part}", "").strip()

        # Limpiar el body eliminando \n y \t
        body_part = clean_body(body_part)
    
    return from_part, subject_part, body_part

Aqui extraemos las partes que componen el email, donde puede estar la primera linea como From o como Subject, de resto es el Body

In [12]:
def process_files_in_folder(folder_path: str = "data/20N"):
    """
    Procesa todos los archivos dentro de la carpeta y extrae la información
    'From', 'Subject' y 'Body' para crear un DataFrame.
    """
    data = []

    # Obtener la lista de carpetas y contar los archivos totales
    total_folders = len([folder for folder in os.listdir(folder_path) if folder != "__init__.py"])
    
    for folder in os.listdir(folder_path):
        if folder != "__init__.py":
            folder_full_path = os.path.join(folder_path, folder)
            files = [file for file in os.listdir(folder_full_path) if file != "__init__.py"]
            total_files = len(files)
            completed_files_in_folder = 0  # Iniciar el conteo por carpeta
            
            # Usar tqdm para mostrar la barra de progreso por carpeta
            for file in tqdm(files, desc=f"Processing files in folder: {folder}", unit="file"):
                with open(os.path.join(folder_full_path, file), 'r') as f:
                    file_content = f.read()

                    # Extraer las partes del archivo
                    from_part, subject_part, body_part = extract_email_parts(file_content)

                    if from_part and body_part:  # Subject es opcional
                        data.append({
                            "category": folder,
                            "email_id": file,
                            'from': from_part,
                            'subject': subject_part,
                            'body': body_part
                        })

                # Incrementar el número de archivos completados en la carpeta
                completed_files_in_folder += 1
                percentage_complete = (completed_files_in_folder / total_files) * 100
                remaining_files = total_files - completed_files_in_folder
                
                # Registrar el progreso correctamente por carpeta
                logger.info(f"Carpeta {folder}: {percentage_complete:.2f}% completado. Restan {remaining_files} archivos en la carpeta.")

    # Convertir la lista de diccionarios en un DataFrame
    df = pd.DataFrame(data)
    return df


Procesamos la informacion para cada una de las carpetas que tiene 20N, extramos la informacion y creamos un df

In [13]:
df_20n = process_files_in_folder()

Processing files in folder: alt.atheism:   0%|          | 0/799 [00:00<?, ?file/s]2024-09-18 10:06:05,636 - INFO - Carpeta alt.atheism: 0.13% completado. Restan 798 archivos en la carpeta.
2024-09-18 10:06:05,638 - INFO - Carpeta alt.atheism: 0.25% completado. Restan 797 archivos en la carpeta.
2024-09-18 10:06:05,639 - INFO - Carpeta alt.atheism: 0.38% completado. Restan 796 archivos en la carpeta.
2024-09-18 10:06:05,639 - INFO - Carpeta alt.atheism: 0.50% completado. Restan 795 archivos en la carpeta.
2024-09-18 10:06:05,640 - INFO - Carpeta alt.atheism: 0.63% completado. Restan 794 archivos en la carpeta.
2024-09-18 10:06:05,641 - INFO - Carpeta alt.atheism: 0.75% completado. Restan 793 archivos en la carpeta.
2024-09-18 10:06:05,641 - INFO - Carpeta alt.atheism: 0.88% completado. Restan 792 archivos en la carpeta.
2024-09-18 10:06:05,643 - INFO - Carpeta alt.atheism: 1.00% completado. Restan 791 archivos en la carpeta.
2024-09-18 10:06:05,644 - INFO - Carpeta alt.atheism: 1.13% co

In [14]:
df_20n.head()

category email_id                                            from  \
0  alt.atheism    49960                    mathew <mathew@mantis.co.uk>   
1  alt.atheism    51060                    mathew <mathew@mantis.co.uk>   
2  alt.atheism    51119  I3150101@dbstu1.rz.tu-bs.de (Benedikt Rosenau)   
3  alt.atheism    51120                    mathew <mathew@mantis.co.uk>   
4  alt.atheism    51121                strom@Watson.Ibm.Com (Rob Strom)   

                                             subject  \
0                 Alt.Atheism FAQ: Atheist Resources   
1           Alt.Atheism FAQ: Introduction to Atheism   
2                                  Re: Gospel Dating   
3  Re: university violating separation of church/...   
4  Re: [soc.motss, et al.] "Princeton axes matchi...   

                                                body  
0  Archive-name: atheism/resources Alt-atheism-ar...  
1  Archive-name: atheism/introduction Alt-atheism...  
2  In article <65974@mimsy.umd.edu> mangoe@cs.umd...  
3  dmn@kepler.unh.edu (...until kings become phil...  
4  In article <N4HY.93Apr5120934@harder.ccr-p.ida...

In [ ]:
df_20n.to_csv("20N_unified.csv")

# Lectura data_reading_BAC

In [2]:
bac_files = 'data/BAC/'

Primero debemos limpiar los datos que tienen entidades HTML esto lo vamos a manejar con bs4 que nos permite trabajar con este tipo de entidades sin eliminarlo manualmente

In [3]:
def clean_and_overwrite_xml(filepath):
    # Intentar abrir el archivo con una codificación más flexible como 'latin-1'
    try:
        with open(filepath, 'r', encoding='utf-8') as file:
            content = file.read()
    except UnicodeDecodeError:
        with open(filepath, 'r', encoding='latin-1') as file:
            content = file.read()

    # Usar BeautifulSoup para manejar entidades HTML dentro del XML
    soup = BeautifulSoup(content, 'xml')

    # Convertir el contenido limpio a una cadena de texto
    cleaned_content = str(soup)

    # Sobrescribir el archivo original con el contenido limpio
    with open(filepath, 'w', encoding='utf-8') as file:
        file.write(cleaned_content)

In [4]:
# Ruta a la carpeta donde están almacenados los archivos XML
ruta_archivos = 'data/BAC/'

# Procesar todos los archivos XML en la carpeta
for archivo in os.listdir(ruta_archivos):
    if archivo.endswith('.xml'):
        archivo_completo = os.path.join(ruta_archivos, archivo)
        clean_and_overwrite_xml(archivo_completo)
        print(f"Archivo procesado: {archivo}")

Archivo procesado: 1000331.female.37.indUnk.Leo.xml
Archivo procesado: 1000866.female.17.Student.Libra.xml
Archivo procesado: 1004904.male.23.Arts.Capricorn.xml
Archivo procesado: 1005076.female.25.Arts.Cancer.xml
Archivo procesado: 1005545.male.25.Engineering.Sagittarius.xml
Archivo procesado: 1007188.male.48.Religion.Libra.xml
Archivo procesado: 100812.female.26.Architecture.Aries.xml
Archivo procesado: 1008329.female.16.Student.Pisces.xml
Archivo procesado: 1009572.male.25.indUnk.Cancer.xml
Archivo procesado: 1011153.female.27.Technology.Virgo.xml
Archivo procesado: 1011289.female.25.indUnk.Libra.xml
Archivo procesado: 1011311.female.17.indUnk.Scorpio.xml
Archivo procesado: 1013637.male.17.RealEstate.Virgo.xml
Archivo procesado: 1015252.female.23.indUnk.Pisces.xml
Archivo procesado: 1015556.male.34.Technology.Virgo.xml
Archivo procesado: 1016560.male.41.Publishing.Sagittarius.xml
Archivo procesado: 1016738.male.26.Publishing.Libra.xml
Archivo procesado: 1016787.female.24.Communicati

Realizamos el procesamiento de los datos de BAC, donde tomamos las columnas como el nombre del archivo es decir, si el nombre es 4334776.male.24.Engineering.Aquarius, entonces las columnas son

* id: 4334776
* gender: male
* age: 24
* profession: Engineering
* zodiac_sign: Aguarius

Para manejar las entradas de los blogs decidimos agregar date, blog_content y number_of_posts. Esto se hizo para no perder informacion de las entradas realizadas por el usuario, de tal forma que, seria una fila en el dataframe por cada fecha que realizo una entrada el usuario. Si hay varias entradas por una fecha, se concatenan con un caracter definido por nosotros como ***POST** *  para identificar en donde empieza la siguiente entrada. Ademas, decidimos crear una funcion para convertir la fecha a formato que python identifique como YYYY-MM-DD

In [36]:
months = {
    # Inglés
    "January": "01", "February": "02", "March": "03", "April": "04", 
    "May": "05", "June": "06", "July": "07", "August": "08", 
    "September": "09", "October": "10", "November": "11", "December": "12",

    # Francés
    "janvier": "01", "février": "02", "mars": "03", "avril": "04", 
    "mai": "05", "juin": "06", "juillet": "07", "août": "08", 
    "septembre": "09", "octobre": "10", "novembre": "11", "décembre": "12",

    # Italiano
    "gennaio": "01", "febbraio": "02", "marzo": "03", "aprile": "04",
    "maggio": "05", "giugno": "06", "luglio": "07", "agosto": "08",
    "settembre": "09", "ottobre": "10", "novembre": "11", "dicembre": "12",

    # Español
    "enero": "01", "febrero": "02", "marzo": "03", "abril": "04",
    "mayo": "05", "junio": "06", "julio": "07", "agosto": "08",
    "septiembre": "09", "octubre": "10", "noviembre": "11", "diciembre": "12",

    # Alemán
    "Januar": "01", "Februar": "02", "März": "03", "April": "04", 
    "Mai": "05", "Juni": "06", "Juli": "07", "August": "08",
    "September": "09", "Oktober": "10", "November": "11", "Dezember": "12",

    # Portugués
    "Janeiro": "01", "Fevereiro": "02", "Março": "03", "Abril": "04",
    "Maio": "05", "Junho": "06", "Julho": "07", "Agosto": "08",
    "Setembro": "09", "Outubro": "10", "Novembro": "11", "Dezembro": "12",

    # Finlandés
    "tammikuu": "01", "helmikuu": "02", "maaliskuu": "03", "huhtikuu": "04",
    "toukokuu": "05", "kesäkuu": "06", "heinäkuu": "07", "elokuu": "08",
    "syyskuu": "09", "lokakuu": "10", "marraskuu": "11", "joulukuu": "12",

    # Polaco
    "styczeń": "01", "luty": "02", "marzec": "03", "kwiecień": "04",
    "maj": "05", "czerwiec": "06", "lipiec": "07", "sierpień": "08",
    "wrzesień": "09", "październik": "10", "listopad": "11", "grudzień": "12",
    
    # Croata/Serbio/Bosnio
    "siječanj": "01", "veljača": "02", "ožujak": "03", "travanj": "04", 
    "svibanj": "05", "lipanj": "06", "srpanj": "07", "kolovoz": "08", 
    "rujan": "09", "listopad": "10", "studeni": "11", "prosinac": "12",

    # Holandés
    "januari": "01", "februari": "02", "maart": "03", "april": "04",
    "mei": "05", "juni": "06", "juli": "07", "augustus": "08",
    "september": "09", "oktober": "10", "november": "11", "december": "12",

    # Rumano
    "ianuarie": "01", "februarie": "02", "martie": "03", "aprilie": "04",
    "mai": "05", "iunie": "06", "iulie": "07", "august": "08",
    "septembrie": "09", "octombrie": "10", "noiembrie": "11", "decembrie": "12",
    
    # Estonio
    "Jaanuar": "01", "Veebruar": "02", "Märts": "03", "Aprill": "04",
    "Mai": "05", "Juuni": "06", "Juuli": "07", "August": "08",
    "September": "09", "Oktoober": "10", "November": "11", "Detsember": "12",
    
    # Otros casos especiales
    "Avgust": "08", "Augusti": "08","augusti": "08","desember": "12","":"00",",":"00"
    }

# Function to convert date from format DD,Month,YYYY to YYYY-MM-DD
def convert_date_to_yyyymmdd(date_str):
    try:
        # Separate the date into day, month, and year
        day, month, year = date_str.split(',')

        # Remove extra spaces and convert the month name to a number
        day = day.strip().zfill(2)  # Ensure the day has two digits
        month = months[month.strip()]
        year = year.strip()

        # Format the date as YYYY-MM-DD
        formatted_date = f"{year}-{month}-{day}"
        
        return formatted_date
    except Exception as e:
        print(f"Error converting date {date_str}: {e}")
        return None



In [37]:
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
import time

In [38]:
def bac_process(filepath, file_index, total_files):
    try:
        start_time = time.time()
        
        # Extraer atributos del nombre del archivo: id, gender, age, profession, zodiac_sign
        filename = os.path.basename(filepath).replace('.xml', '')
        columns = filename.split('.')

        if len(columns) != 5:
            raise ValueError(f"El archivo {filename} no tiene el formato adecuado.")

        id_, gender, age, profession, zodiac_sign = columns

        # Intentar abrir el archivo con una codificación más flexible como 'latin-1'
        try:
            with open(filepath, 'r', encoding='utf-8') as file:
                content = file.read()
        except UnicodeDecodeError:
            with open(filepath, 'r', encoding='latin-1') as file:
                content = file.read()

        # Usar BeautifulSoup para manejar el XML
        soup = BeautifulSoup(content, 'xml')

        # Extraer todas las dates y las publicaciones
        dates = [date.text for date in soup.find_all('date')]
        publicaciones = [post.text.strip() for post in soup.find_all('post')]

        # Agrupar las publicaciones por su fecha
        post_by_date = defaultdict(list)
        for fecha, publicacion in zip(dates, publicaciones):
            post_by_date[fecha].append(publicacion)

        # Preparar los datos para el DataFrame
        data = []
        for fecha, posts in post_by_date.items():
            # Concatenar las publicaciones con 'POST' y contar el número de publicaciones
            blog_content = ' '.join(posts)
            number_of_posts = len(posts)
            
            formatted_date = convert_date_to_yyyymmdd(fecha)

            # Agregar una fila al conjunto de datos
            data.append([id_, gender, age, profession, zodiac_sign, formatted_date, blog_content, number_of_posts])

        # Crear un DataFrame para este archivo
        df = pd.DataFrame(data, columns=['id', 'gender', 'age', 'profession', 'zodiac_sign', 'date', 'blog_content', 'number_of_posts'])

        # Registro del progreso
        elapsed_time = time.time() - start_time
        remaining_files = total_files - file_index - 1
        logging.info(f"Archivo {file_index + 1}/{total_files} procesado en {elapsed_time:.2f} segundos. Faltan {remaining_files} archivos.")
        
        return df

    except Exception as e:
        logging.error(f"Error al procesar {filepath}: {e}")
        return pd.DataFrame()

# Ruta a la carpeta donde están almacenados los archivos XML
ruta_archivos = 'data/BAC/'

# Lista para almacenar los DataFrames de todos los archivos
df_list = []

# Obtener la lista de archivos en la carpeta
archivos = [archivo for archivo in os.listdir(ruta_archivos) if archivo.endswith('.xml')]
total_files = len(archivos)

# Procesar todos los archivos XML en la carpeta
for file_index, archivo in enumerate(archivos):
    archivo_completo = os.path.join(ruta_archivos, archivo)
    df = bac_process(archivo_completo, file_index, total_files)
    if not df.empty:
        df_list.append(df)


2024-09-18 12:06:39,865 - INFO - Archivo 1/19320 procesado en 0.00 segundos. Faltan 19319 archivos.
2024-09-18 12:06:39,899 - INFO - Archivo 2/19320 procesado en 0.03 segundos. Faltan 19318 archivos.
2024-09-18 12:06:39,903 - INFO - Archivo 3/19320 procesado en 0.00 segundos. Faltan 19317 archivos.
2024-09-18 12:06:39,906 - INFO - Archivo 4/19320 procesado en 0.00 segundos. Faltan 19316 archivos.
2024-09-18 12:06:39,912 - INFO - Archivo 5/19320 procesado en 0.00 segundos. Faltan 19315 archivos.
2024-09-18 12:06:39,915 - INFO - Archivo 6/19320 procesado en 0.00 segundos. Faltan 19314 archivos.
2024-09-18 12:06:39,920 - INFO - Archivo 7/19320 procesado en 0.00 segundos. Faltan 19313 archivos.
2024-09-18 12:06:39,925 - INFO - Archivo 8/19320 procesado en 0.01 segundos. Faltan 19312 archivos.
2024-09-18 12:06:39,926 - INFO - Archivo 9/19320 procesado en 0.00 segundos. Faltan 19311 archivos.
2024-09-18 12:06:39,928 - INFO - Archivo 10/19320 procesado en 0.00 segundos. Faltan 19310 archivos.

In [39]:
# Concatenar todos los DataFrames en uno solo
df_bac = pd.concat(df_list, ignore_index=True)

df_bac.to_csv('bac_unified.csv', index=False)


In [28]:
df_bac.head()

id  gender age profession zodiac_sign        date  \
0  1000331  female  37     indUnk         Leo  2004-05-31   
1  1000331  female  37     indUnk         Leo  2004-05-29   
2  1000331  female  37     indUnk         Leo  2004-05-28   
3  1000331  female  37     indUnk         Leo  2004-06-21   
4  1000331  female  37     indUnk         Leo  2004-06-18   

                                        blog_content  number_of_posts  
0  Well, everyone got up and going this morning. ...                1  
1  My four-year old never stops talking.  She'll ...                1  
2  Actually it's not raining yet, but I bought 15...                4  
3  My 20th high school  urlLink reunion  is this ...                1  
4  We always have pizza on Friday nights.  It tak...                1

In [34]:
for i in df_bac['blog_content'][2].split(" "):
    if "POST" in i:
        print(i)

is!POSTHa!
promise.POSTOh,
case!POSTI've


# PROCESO DE TOKENIZADO

## PROCESO DE TOKENIZADO PARA DATOS 20N

In [52]:
#Selecciónn de columna correspondiente a las oraciones
body_20n = df_20n[['body']]

### Funciones básicas de tokenizado

La función normalize_text se encarga de convertir a todas las letras de las oraciones en minúsculas, y posteriormente elimina todos los caracteres especiales como las comas y los puntos y separa cada signo de puntuación con un espacio

La función words_to_numbers maneja un caso excepcional para convertir palabras que representen números como dígitos, para ello utiliza la librería text2num para convertir las palabras que sean necesarias a lo largo del corpus

La función replace_digits se encarga de convertir todos los digitos del corpus en el caracter NUM

In [53]:
def normalize_text(text):
    text = text.lower()
    text = re.sub(r'[^\w\s]', ' ', text)
    return text

def words_to_numbers(token):
    try:
        return str(text2num(token,'en'))
    except ValueError:
        return token

def replace_digits(token):
    if token.isdigit():
        return 'NUM'
    return token


En primer lugar, se aplica la normalización antes de realizar el tokenizado de palabras

In [54]:
body_20n['normalized'] = body_20n['body'].apply(normalize_text)

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/3604201721.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_20n['normalized'] = body_20n['body'].apply(normalize_text)


Posteriormente, se hace una tokenización con la librería word_tokenize de nltk

In [57]:
body_20n['tokenized'] = body_20n['normalized'].apply(word_tokenize)

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/814313017.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_20n['tokenized'] = body_20n['normalized'].apply(word_tokenize)


Luego, se realiza el reemplazo de palabras que representen dígitos en dígitos, esto con el objetivo de facilitar la conversión de dígitos en caracteres NUM en el siguiente paso

In [58]:
body_20n['digits'] = body_20n['tokenized'].apply(lambda tokens: [words_to_numbers(token) for token in tokens])

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/282450380.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_20n['digits'] = body_20n['tokenized'].apply(lambda tokens: [words_to_numbers(token) for token in tokens])


Luego de haber hecho el reemplazo de palabras, se hace el reemplazo de todos los dígitos en un caracter denominado NUM

In [59]:
body_20n['replacement'] = body_20n['digits'].apply(lambda tokens: [replace_digits(token) for token in tokens])

Se añade un <s> al comienzo de cada oración y se añade un </S> al término de cada oración

In [60]:
body_20n['sentence'] = body_20n['replacement'].apply(lambda tokens: ['<s>'] + tokens + ['</s>'])

Por último, se realiza un conteo de todos los tokens en el corpus, si un token sólo aparece una vez, entonces se reemplaza por el caracter <UNK>

In [76]:
all_tokens = [token for tokens in body_20n['sentence'] for token in tokens]
token_freq = Counter(all_tokens)

def replace_unique_tokens(tokens, freq_dict):
    return [token if freq_dict[token] > 1 else '<UNK>' for token in tokens]


Reemplazo del token en el dataframe

In [77]:
body_20n['unique'] = body_20n['sentence'].apply(lambda tokens: replace_unique_tokens(tokens, token_freq))

Exportación de resultados obtenidos para realizar la división de datos

In [83]:
results_20n = pd.DataFrame(body_20n['unique'].apply(lambda tokens: ' '.join(tokens)))

In [124]:
results_20n.to_csv("20n_tokenized.csv",index=False)

In [78]:
body_20n

body  \
0      Archive-name: atheism/resources Alt-atheism-ar...   
1      Archive-name: atheism/introduction Alt-atheism...   
2      In article <65974@mimsy.umd.edu> mangoe@cs.umd...   
3      dmn@kepler.unh.edu (...until kings become phil...   
4      In article <N4HY.93Apr5120934@harder.ccr-p.ida...   
...                                                  ...   
18789  pboxrud@magnus.acs.ohio-state.edu (Paul D Boxr...   
18790  In article <1993Apr23.111105.7703@ifi.uio.no>,...   
18791  In article <1rc1f3INN7rl@emx.cc.utexas.edu> bi...   
18792  In article <1993Apr26.231845.13843@digi.lonest...   
18793  In article <C64H4w.BFH@darkside.osrhe.uoknor.e...   

                                              normalized  \
0      archive name  atheism resources alt atheism ar...   
1      archive name  atheism introduction alt atheism...   
2      in article  65974 mimsy umd edu  mangoe cs umd...   
3      dmn kepler unh edu     until kings become phil...   
4      in article  n4hy 93apr5120934 harder ccr p ida...   
...                                                  ...   
18789  pboxrud magnus acs ohio state edu  paul d boxr...   
18790  in article  1993apr23 111105 7703 ifi uio no  ...   
18791  in article  1rc1f3inn7rl emx cc utexas edu  bi...   
18792  in article  1993apr26 231845 13843 digi lonest...   
18793  in article  c64h4w bfh darkside osrhe uoknor e...   

                                               tokenized  \
0      [archive, name, atheism, resources, alt, athei...   
1      [archive, name, atheism, introduction, alt, at...   
2      [in, article, 65974, mimsy, umd, edu, mangoe, ...   
3      [dmn, kepler, unh, edu, until, kings, become, ...   
4      [in, article, n4hy, 93apr5120934, harder, ccr,...   
...                                                  ...   
18789  [pboxrud, magnus, acs, ohio, state, edu, paul,...   
18790  [in, article, 1993apr23, 111105, 7703, ifi, ui...   
18791  [in, article, 1rc1f3inn7rl, emx, cc, utexas, e...   
18792  [in, article, 1993apr26, 231845, 13843, digi, ...   
18793  [in, article, c64h4w, bfh, darkside, osrhe, uo...   

                                                  digits  \
0      [archive, name, atheism, resources, alt, athei...   
1      [archive, name, atheism, introduction, alt, at...   
2      [in, article, 65974, mimsy, umd, edu, mangoe, ...   
3      [dmn, kepler, unh, edu, until, kings, become, ...   
4      [in, article, n4hy, 93apr5120934, harder, ccr,...   
...                                                  ...   
18789  [pboxrud, magnus, acs, ohio, state, edu, paul,...   
18790  [in, article, 1993apr23, 111105, 7703, ifi, ui...   
18791  [in, article, 1rc1f3inn7rl, emx, cc, utexas, e...   
18792  [in, article, 1993apr26, 231845, 13843, digi, ...   
18793  [in, article, c64h4w, bfh, darkside, osrhe, uo...   

                                             replacement  \
0      [archive, name, atheism, resources, alt, athei...   
1      [archive, name, atheism, introduction, alt, at...   
2      [in, article, NUM, mimsy, umd, edu, mangoe, cs...   
3      [dmn, kepler, unh, edu, until, kings, become, ...   
4      [in, article, n4hy, 93apr5120934, harder, ccr,...   
...                                                  ...   
18789  [pboxrud, magnus, acs, ohio, state, edu, paul,...   
18790  [in, article, 1993apr23, NUM, NUM, ifi, uio, n...   
18791  [in, article, 1rc1f3inn7rl, emx, cc, utexas, e...   
18792  [in, article, 1993apr26, NUM, NUM, digi, lones...   
18793  [in, article, c64h4w, bfh, darkside, osrhe, uo...   

                                                sentence  \
0      [<s>, archive, name, atheism, resources, alt, ...   
1      [<s>, archive, name, atheism, introduction, al...   
2      [<s>, in, article, NUM, mimsy, umd, edu, mango...   
3      [<s>, dmn, kepler, unh, edu, until, kings, bec...   
4      [<s>, in, article, n4hy, 93apr5120934, harder,...   
...                                                  ...   
18789  [<s>, pboxrud, magnu

## PROCESO DE TOKENIZADO PARA DATOS BAC

Se utilizó el mismo proceso de tokenización de los datos 20N, en este caso sólo se utilizo el llamado de funciones puesto a que las funciones ya fueron creadas para los datos anteriores

In [107]:
df_bac = pd.read_csv("bac_unified.csv")

In [108]:
df_bac

id  gender  age profession zodiac_sign        date  \
0       1000331  female   37     indUnk         Leo  2004-05-31   
1       1000331  female   37     indUnk         Leo  2004-05-29   
2       1000331  female   37     indUnk         Leo  2004-05-28   
3       1000331  female   37     indUnk         Leo  2004-06-21   
4       1000331  female   37     indUnk         Leo  2004-06-18   
...         ...     ...  ...        ...         ...         ...   
331396   999503    male   25   Internet      Cancer  2004-07-05   
331397   999503    male   25   Internet      Cancer  2004-07-04   
331398   999503    male   25   Internet      Cancer  2004-07-03   
331399   999503    male   25   Internet      Cancer  2004-07-02   
331400   999503    male   25   Internet      Cancer  2004-07-01   

                                             blog_content  number_of_posts  
0       Well, everyone got up and going this morning. ...                1  
1       My four-year old never stops talking.  She'll ...                1  
2       Actually it's not raining yet, but I bought 15...                4  
3       My 20th high school  urlLink reunion  is this ...                1  
4       We always have pizza on Friday nights.  It tak...                1  
...                                                   ...              ...  
331396  Chillin to some groove salad, studying BGP con...                1  
331397  Today we celebrate our independence day.    In...                1  
331398  Ugh, I think I have allergies...  My nose has ...                1  
331399  "Science is like sex; occasionally something p...                1  
331400  urlLink Dog toy or marital aid   I managed 10/...                2  

[331401 rows x 8 columns]

In [109]:
body_bac = df_bac[['blog_content']]

Conversión de texto del archivo BAC como strings para evitar errores en futuros pasos

In [118]:
body_bac['blog_content'] = body_bac[['blog_content']].astype(str)

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/3623974741.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['blog_content'] = body_bac[['blog_content']].astype(str)


In [119]:
#Conjunto de oraciones
body_bac

blog_content
0       Well, everyone got up and going this morning. ...
1       My four-year old never stops talking.  She'll ...
2       Actually it's not raining yet, but I bought 15...
3       My 20th high school  urlLink reunion  is this ...
4       We always have pizza on Friday nights.  It tak...
...                                                   ...
331396  Chillin to some groove salad, studying BGP con...
331397  Today we celebrate our independence day.    In...
331398  Ugh, I think I have allergies...  My nose has ...
331399  "Science is like sex; occasionally something p...
331400  urlLink Dog toy or marital aid   I managed 10/...

[331401 rows x 1 columns]

Se aplica la misma función de normalización que se utilizó para datos 20N

In [120]:
body_bac['normalized'] = body_bac['blog_content'].apply(normalize_text)

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/2090022200.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['normalized'] = body_bac['blog_content'].apply(normalize_text)


Se aplica word_tokenize de la librería nltk

In [122]:
body_bac['tokenized'] = body_bac['normalized'].apply(word_tokenize)

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/1310342155.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['tokenized'] = body_bac['normalized'].apply(word_tokenize)


Se aplica el reemplazo de palabras a dígitos

In [125]:
body_bac['digits'] = body_bac['tokenized'].apply(lambda tokens: [words_to_numbers(token) for token in tokens])

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/757422033.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['digits'] = body_bac['tokenized'].apply(lambda tokens: [words_to_numbers(token) for token in tokens])


Se aplica el reemplazo de dígitos al caracter NUM

In [126]:
body_bac['replacement'] = body_bac['digits'].apply(lambda tokens: [replace_digits(token) for token in tokens])

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/1313792504.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['replacement'] = body_bac['digits'].apply(lambda tokens: [replace_digits(token) for token in tokens])


Se añade <s> al comienzo de cada frase y </s> al término de cada frase

In [127]:
body_bac['sentence'] = body_bac['replacement'].apply(lambda tokens: ['<s>'] + tokens + ['</s>'])

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/4251335818.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['sentence'] = body_bac['replacement'].apply(lambda tokens: ['<s>'] + tokens + ['</s>'])


Se aplica el mismo proceso para el reemplazo de tokens únicos en todo el corpus

In [128]:
all_tokens = [token for tokens in body_bac['sentence'] for token in tokens]
token_freq = Counter(all_tokens)

In [131]:
body_bac['unique'] = body_bac['sentence'].apply(lambda tokens: replace_unique_tokens(tokens, token_freq))

/var/folders/j2/dt9fh71s1yq44ph9g2dysl4r0000gn/T/ipykernel_77944/462386146.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  body_bac['unique'] = body_bac['sentence'].apply(lambda tokens: replace_unique_tokens(tokens, token_freq))


Se exportan los datos a un dataframe único en un csv

In [132]:
results_bac = pd.DataFrame(body_bac['unique'].apply(lambda tokens: ' '.join(tokens)))

In [133]:
results_bac.to_csv("bac_tokenized.csv",index=False)

# DIVISIÓN DE DATOS

Se utilizó la librería train_test_split de scikit-learn para realizar la división aleatoria de datos, se hizo la división correspondiente de 80% para entrenamiento y 20% para prueba para ambos archivos

## DIVISIÓN DE DATOS - 20N

In [ ]:
#lectura de archivo tokenizadoo
df_20n = pd.read_csv("20n_tokenized.csv")

In [ ]:
#División de datos 80% - 20%
train_20n, test_20n = train_test_split(df_20n, train_size=0.8, random_state=42)

Se exportan los datos obtenidos de la división a un csv

In [ ]:
train_20n.to_csv("20N_01_training.csv")
test_20n.to_csv("20N_01_testing.csv")

## DIVISIÓN DE DATOS - BAC

In [ ]:
#lectura de archivoo
df_bac = pd.read_csv("bac_tokenized.csv")

In [ ]:
#División de datos 80% - 20%
train_bac, test_bac = train_test_split(df_bac, train_size=0.8, random_state=42)

Se exportan los datos obtenidos de la división a un csv

In [ ]:
train_bac.to_csv("BAC_01_training.csv")
test_bac.to_csv("BAC_01_testing.csv")